In [1]:
%load_ext autoreload
%autoreload 2

import pathlib
if pathlib.Path().resolve().name == 'notebooks':
    %cd ..
%pwd

/Users/alexandreganito/Documents/Data science/Project/NHL


'/Users/alexandreganito/Documents/Data science/Project/NHL'

In [158]:
import plotly.graph_objects as go
import plotly.express as px
import pandas as pd
import numpy as np
from scipy import stats
from PIL import Image
from src.utils import normalize
from src.data import load_df_shots

In [139]:
year = 2017
df = load_df_shots(year)
df

Game_id  Period   Time Team   Goal     X     Y         Shooter  \
0            1       1  00:38  WPG  False -36.0 -28.0  Josh Morrissey   
1            1       1  00:49  WPG  False -75.0   1.0  Shawn Matthias   
2            1       1  01:03  WPG  False -73.0  10.0    Bryan Little   
3            1       1  01:46  TOR  False  80.0  -3.0       Eric Fehr   
4            1       1  03:42  WPG  False -44.0 -21.0    Patrik Laine   
...        ...     ...    ...  ...    ...   ...   ...             ...   
81860     1271       3  18:10  SJS  False  52.0  35.0      Timo Meier   
81861     1271       3  18:50  SJS   True  29.0 -10.0      Timo Meier   
81862     1271       3  19:22  SJS  False  31.0 -16.0     Brent Burns   
81863     1271       3  19:25  SJS  False  80.0  -8.0    Joe Pavelski   
81864     1271       3  19:34  MIN   True   0.0 -24.0      Eric Staal   

                  Goalie        Type Empty_net Strength  X_dist  Net_distance  
0      Frederik Andersen  Wrist Shot      None             53.0     59.941638  
1      Frederik Andersen  Wrist Shot      None             14.0     14.035669  
2      Frederik Andersen    Backhand      None             16.0     18.867962  
3            Steve Mason  Wrist Shot      None              9.0      9.486833  
4      Frederik Andersen   Snap Shot      None             45.0     49.658836  
...                  ...         ...       ...      ...     ...           ...  
81860       Devan Dubnyk   Snap Shot      None             37.0     50.931326  
81861       Devan Dubnyk   Deflected     False     Even    60.0     60.827625  
81862       Devan Dubnyk  Wrist Shot      None             58.0     60.166436  
81863       Devan Dubnyk  Wrist Shot      None              9.0     12.041595  
81864                      Snap Shot      True     Even    89.0     92.179173  

[81865 rows x 14 columns]

In [90]:
def get_shots_location(df, team):
    df_tot = df[df.X_dist < 90]
    df_team = df_tot[df_tot.Team == team]
    df_tot = df_tot.groupby(['X_dist', 'Y']).size().to_frame('Counts').reset_index()
    df_tot = df_tot.pivot(index='X_dist', columns='Y')['Counts'].fillna(0)
    df_tot = df_tot / (df.Game_id.nunique() * 2)
    df_tot = pd.melt(df_tot.reset_index(), id_vars='X_dist', value_vars=df_tot.columns)

    df_team = df_team.groupby(['X_dist', 'Y']).size().to_frame('Counts').reset_index()
    df_team = df_team.pivot(index='X_dist', columns='Y')['Counts'].fillna(0)
    df_team = df_team / 82
    df_team = pd.melt(df_team.reset_index(), id_vars='X_dist', value_vars=df_team.columns)

    df_sl = pd.merge(df_tot, df_team, on=["X_dist", "Y"],  how="outer").fillna(0)
    df_sl["dif"] = df_sl.value_y - df_sl.value_x

    df_sl['ybin'] = pd.cut(df_sl.Y, 15)
    df_sl['xbin'] = pd.cut(df_sl.X_dist, 15)
    df_sl['dif_bin'] = df_sl.groupby(['xbin', 'ybin'], observed=True).dif.transform('sum')

    return df_sl

In [100]:
def get_dens(team):
    dfs = get_shots_location(df, team)
    max = dfs.dif_bin.max()

    values = [dfs.X_dist.values, dfs.Y.values]
    weights_tot = dfs.value_x.values
    weights_team = dfs.value_y.values

    gauss_tot = stats.gaussian_kde(values, bw_method=0.3,weights=weights_tot)
    gauss_team = stats.gaussian_kde(values, bw_method=0.3,weights=weights_team)


    x = np.linspace(0, 89, 90)
    y = np.linspace(-42, 42, 85)
    X, Y = np.meshgrid(x, y)
    xy = np.vstack([X.ravel(), Y.ravel()])
    dens_tot = np.exp(gauss_tot(xy)).reshape((X.shape))
    dens_team= np.exp(gauss_team(xy)).reshape((X.shape))

    dens = dens_team - dens_tot

    ratio = np.array(dens).reshape(-1).min() / np.array(dens).reshape(-1).max()
    return normalize(np.flip(dens), max * ratio, max)



In [157]:
pyLogo = Image.open("figures/half_nhl_rink.png")

fig = go.Figure()

x = np.linspace(0, 89, 90)
y = np.linspace(-42, 42, 85)

teams = df.Team.unique()
visibility = [False] * len(teams)
dropdown_list = []

fig.add_trace(
    go.Contour(
        z=get_dens(teams[0]),
        # z=np.flip(dens_team - dens_tot),
        x=x, 
        y=y,
        opacity = 0.6,
        colorscale='RdBu_r',
        contours_coloring='fill',  # This will fill the contours
        contours=dict(start=-0.5, end=0.5, size=0.05),  # You can adjust these parameters
        visible=True
    )
)

vis = visibility.copy()
vis[0] = True

dropdown_list.append(dict(
                args=[{"visible": vis}],
                label=teams[0],
                method="restyle"
            ))

for id, team in enumerate(teams[1:]):


# Plotly Contour Plot
    fig.add_trace(
        go.Contour(
            z=get_dens(team),
            x=x, 
            y=y,
            opacity = 0.6,
            colorscale='RdBu_r',
            contours_coloring='fill',
            contours=dict(start=-0.5, end=0.5, size=0.05),
            visible=False
        )
    )

    vis = visibility.copy()
    vis[id + 1] = True

    dropdown_list.append(dict(
                    args=[{"visible": vis}],
                    label=team,
                    method="restyle"
                ))


fig.update_layout(
    height=600,
    width=680,
    title = f'Season {year}',
    title_font_size=30,
    updatemenus=[
        dict(
            active=0,
            buttons=dropdown_list,
            showactive=True,
            x=0.35,
            xanchor="left",
            y=1.18,
            yanchor="top"
        ),
    ]
)
fig.add_layout_image(
        dict(
            source=pyLogo,
            xref="x",
            yref="y",
            x=0,
            y=42.5,
            sizex=100,
            sizey=85,
            opacity=1,
            layer="below")
)

fig.update_xaxes(showline=False, zeroline=False, showgrid=False, range=[0, 100])
fig.update_yaxes(
    showline=False,
    zeroline=False,
    showgrid=False,
    range=[-42.5, 42.5],
    scaleanchor = "x",
    scaleratio = 1,
  )

fig.show()
# fig.write_html(f'figures/shots{year}.html')